# Run a Template Job

This notebook demonstrates how to run a customizable job using a template.

## Imports

As in every notebook we make, first import the various packages needed for the rest of the notebook function.

In [1]:
from webmo import WebMOREST
from webmo.util import xyz_from_name
from webmo.gui import JupyterGUI

## User Setup

Set up the user-supplied information that defines the job.

In [2]:
## BOOKKEEPING PARAMETERS
# the URL of your WebMO instance
URL = "https://server.university.edu/~webmo/cgi-bin/webmo/rest.cgi"

# your username on the above WebMO instance
username = "smith"

## JOB PARAMETERS
# name of the molecule to run a job on
molecule = "methane"

# job type to run
job_type = "Optimize + Vib Freq" 

## Geometry

Grab the 3D geometry from PubChem.

In [3]:
geom = xyz_from_name(molecule)

## REST session

Open a WebMO REST session.

In [4]:
rest = WebMOREST(URL, username=username)

Enter WebMO password for user smith: ········


## Template

Create the job template and submit it using the new GUI module.

In [5]:
gui = JupyterGUI(rest.get_templates("gaussian")[job_type],
                query_vars=[
                    "jobName",
                    "basisSet",
                    "theory",
                    "multiplicity",
                    "charge",
                ],
                additional_vars={
                    "geometry":geom
                })

In [6]:
gui.display()

Text(value='Title', description='jobName')

Dropdown(description='basisSet', index=3, options={'Accurate: 6-311+G(2d,p)': '6-311+G(2d,p)', 'cc-pVTZ': 'cc-…

Dropdown(description='theory', options={'Hartree-Fock': 'HF', 'UFF Mechanics': 'UFF', 'APF-D': 'APFD', 'PM6': …

Dropdown(description='multiplicity', index=2, options={'Triplet': '3', 'Quartet': '4', 'Singlet': '1', 'Quinte…

Text(value='0', description='charge')

In [7]:
job = rest.generate_input(rest.get_templates("gaussian")[job_type], gui.get_variables())

print("The job that will be submitted:")
print(job)

The job that will be submitted:
#N MP2/3-21G OPT FREQ 

Methane Opt Freq

0 1
C	0.000000	0.000000	0.000000
H	0.554100	0.799600	0.496500
H	0.683300	-0.813400	-0.253600
H	-0.778200	-0.373500	0.669200
H	-0.459300	0.387400	-0.912100




Submit the job through that REST session and wait for it to complete.

In [8]:
n = rest.submit_job(gui.get_variables()['jobName'], job, "gaussian")
rest.wait_for_job(n)

After the job is finished, get some of its output.

In [9]:
print(rest.get_job_output(n)[:400])

 Entering Gaussian System, Link 0=/share/apps/g16/g16
 Initial command:
 /share/apps/g16/l1.exe "/scratch/webmo-1316028/40/Gau-990953.inp" -scrdir="/scratch/webmo-1316028/40/"
 Entering Link 1 = /share/apps/g16/l1.exe PID=    990954.
  
 Copyright (c) 1988-2019, Gaussian, Inc.  All Rights Reserved.
  
 This is part of the Gaussian(R) 16 program.  It is based on
 the Gaussian(R) 09 system (copyrigh


We can also get numeric results through the WebMO library, such as the energy.

In [10]:
results = rest.get_job_results(n)
energy = results['properties']['rhf_energy']['value']
units = results['properties']['rhf_energy']['units']
print("Energy: {} {}".format(energy, units))

Energy: -39.9766423976 Hartree
